In [12]:
import json
import os
import numpy as np
dir_name='./Kitti/training/label_2/'
all_dicts={}
for filename in sorted(os.listdir(dir_name)):
    temp_list=[]
    with open (dir_name+filename) as f:
        filename=filename.replace(".txt","")
        for line in f:
            line=line.split()
            temp_list.append({'class':line[0],
                  'alpha':line[3],
                  'boxs':line[4:8],
            '3d_attribute':line[8:15],
            'new_3d_pos':[0 ,0 ,0],
            })
        all_dicts[filename]=temp_list
        #

In [2]:
all_dicts['000001']

[{'class': 'Truck',
  'alpha': '-1.57',
  'boxs': ['599.41', '156.40', '629.75', '189.25'],
  '3d_attribute': ['2.85', '2.63', '12.34', '0.47', '1.49', '69.44', '-1.56'],
  'new_3d_pos': [0, 0, 0]},
 {'class': 'Car',
  'alpha': '1.85',
  'boxs': ['387.63', '181.54', '423.81', '203.12'],
  '3d_attribute': ['1.67', '1.87', '3.69', '-16.53', '2.39', '58.49', '1.57'],
  'new_3d_pos': [0, 0, 0]},
 {'class': 'Cyclist',
  'alpha': '-1.65',
  'boxs': ['676.60', '163.95', '688.98', '193.93'],
  '3d_attribute': ['1.86', '0.60', '2.02', '4.59', '1.32', '45.84', '-1.55'],
  'new_3d_pos': [0, 0, 0]},
 {'class': 'DontCare',
  'alpha': '-10',
  'boxs': ['503.89', '169.71', '590.61', '190.13'],
  '3d_attribute': ['-1', '-1', '-1', '-1000', '-1000', '-1000', '-10'],
  'new_3d_pos': [0, 0, 0]},
 {'class': 'DontCare',
  'alpha': '-10',
  'boxs': ['511.35', '174.96', '527.81', '187.45'],
  '3d_attribute': ['-1', '-1', '-1', '-1000', '-1000', '-1000', '-10'],
  'new_3d_pos': [0, 0, 0]},
 {'class': 'DontCar

In [3]:
for filename  in sorted(os.listdir(dir_name)):
    with open (dir_name+filename) as f:
        filename=filename.replace(".txt","")
        for line in f:
            line=line.split()
            print(line[3:15])
        print(filename)
       

['-0.20', '712.40', '143.00', '810.73', '307.92', '1.89', '0.48', '1.20', '1.84', '1.47', '8.41', '0.01']
000000
['-1.57', '599.41', '156.40', '629.75', '189.25', '2.85', '2.63', '12.34', '0.47', '1.49', '69.44', '-1.56']
['1.85', '387.63', '181.54', '423.81', '203.12', '1.67', '1.87', '3.69', '-16.53', '2.39', '58.49', '1.57']
['-1.65', '676.60', '163.95', '688.98', '193.93', '1.86', '0.60', '2.02', '4.59', '1.32', '45.84', '-1.55']
['-10', '503.89', '169.71', '590.61', '190.13', '-1', '-1', '-1', '-1000', '-1000', '-1000', '-10']
['-10', '511.35', '174.96', '527.81', '187.45', '-1', '-1', '-1', '-1000', '-1000', '-1000', '-10']
['-10', '532.37', '176.35', '542.68', '185.27', '-1', '-1', '-1', '-1000', '-1000', '-1000', '-10']
['-10', '559.62', '175.83', '575.40', '183.15', '-1', '-1', '-1', '-1000', '-1000', '-1000', '-10']
000001
['-1.82', '804.79', '167.34', '995.43', '327.94', '1.63', '1.48', '2.37', '3.23', '1.59', '8.55', '-1.47']
['-1.67', '657.39', '190.13', '700.07', '223.39'

In [13]:
def rotation_matrix(yaw, pitch=0, roll=0):
    tx = roll
    ty = yaw
    tz = pitch

    Rx = np.array([[1,0,0], [0, np.cos(tx), -np.sin(tx)], [0, np.sin(tx), np.cos(tx)]])
    Ry = np.array([[np.cos(ty), 0, np.sin(ty)], [0, 1, 0], [-np.sin(ty), 0, np.cos(ty)]])
    Rz = np.array([[np.cos(tz), -np.sin(tz), 0], [np.sin(tz), np.cos(tz), 0], [0,0,1]])


    return Ry.reshape([3,3])

In [14]:
for key,file in all_dicts.items():
    for index,info in enumerate(file):
        file[index]['alpha']=(float(file[index]['alpha']))
        file[index]['boxs']=list(map(float,file[index]['boxs']))
        file[index]['3d_attribute']=list(map(float,file[index]['3d_attribute']))


In [84]:
def cal_math(all_dicts):
    for file_num in range(len(all_dicts)):

        yaw_angle=(all_dicts[file_num]['3d_attribute'][6])
        alpha=all_dicts[file_num]['alpha']
        xmin = int(all_dicts[file_num]['boxs'][0])
        ymin = int(all_dicts[file_num]['boxs'][1])
        xmax = int(all_dicts[file_num]['boxs'][2])
        ymax =int(all_dicts[file_num]['boxs'][3])
        box_corners = [xmin, ymin, xmax, ymax]
        dimension=all_dicts[file_num]['3d_attribute'][0:3]
        R=rotation_matrix(yaw_angle)

        proj_matrix= np.array([[ 7.188560e+02 , 0.000000e+00 , 6.071928e+02 , 4.538225e+01],
        [ 0.000000e+00 , 7.188560e+02 , 1.852157e+02, -1.130887e-01],
        [ 0.000000e+00 , 0.000000e+00,  1.000000e+00 , 3.779761e-03]])
        

        constraints = []

        left_constraints = []
        right_constraints = []
        top_constraints = []
        bottom_constraints = []

        # using a different coord system
        dx = dimension[2] / 2
        dy = dimension[0] / 2
        dz = dimension[1] / 2

        # below is very much based on trial and error

        # based on the relative angle, a different configuration occurs
        # negative is back of car, positive is front
        left_mult = 1
        right_mult = -1

        if alpha < np.deg2rad(92) and alpha > np.deg2rad(88):
            left_mult = 1
            right_mult = 1
        # about straight on and same way
        elif alpha < np.deg2rad(-88) and alpha > np.deg2rad(-92):
            left_mult = -1
            right_mult = -1
        # this works but doesnt make much sense
        elif alpha < np.deg2rad(90) and alpha > -np.deg2rad(90):
            left_mult = -1
            right_mult = 1

        # if the car is facing the oppositeway, switch left and right
        switch_mult = -1
        if alpha > 0:
            switch_mult = 1

        for i in (-1,1):
            left_constraints.append([left_mult * dx, i*dy, -switch_mult * dz])
        for i in (-1,1):
            right_constraints.append([right_mult * dx, i*dy, switch_mult * dz])

        # top and bottom are easy, just the top and bottom of car
        for i in (-1,1):
            for j in (-1,1):
                top_constraints.append([i*dx, -dy, j*dz])

        for i in (-1,1):
            for j in (-1,1):
                bottom_constraints.append([i*dx, dy, j*dz])

        for left in left_constraints:
            for top in top_constraints:
                for right in right_constraints:
                    for bottom in bottom_constraints:
                        constraints.append([left, top, right, bottom])

        constraints = filter(lambda x: len(x) == len(set(tuple(i) for i in x)), constraints)

        # create pre M (the term with I and the R*X)
        pre_M = np.zeros([4,4])
        # 1's down diagonal
        for i in range(0,4):
            pre_M[i][i] = 1

        best_loc = None
        best_error = [1e09]
        best_X = None

        count = 0
        for constraint in constraints:
            # each corner
            Xa = constraint[0]
            Xb = constraint[1]
            Xc = constraint[2]
            Xd = constraint[3]

            X_array = [Xa, Xb, Xc, Xd]

            # M: all 1's down diagonal, and upper 3x1 is Rotation_matrix * [x, y, z]
            Ma = np.copy(pre_M)
            Mb = np.copy(pre_M)
            Mc = np.copy(pre_M)
            Md = np.copy(pre_M)

            M_array = [Ma, Mb, Mc, Md]

            # create A, b
            A = np.zeros([4,3], dtype=np.float)
            b = np.zeros([4,1])

            indicies = [0,1,0,1]
            for row, index in enumerate(indicies):
                X = X_array[row]
                M = M_array[row]

                # create M for corner Xx
                RX = np.dot(R, X)
                M[:3,3] = RX.reshape(3)

                M = np.dot(proj_matrix, M)

                A[row, :] = M[index,:3] - box_corners[row] * M[2,:3]
                b[row] = box_corners[row] * M[2,3] - M[index,3]

            # solve here with least squares, since over fit will get some error
            loc, error, rank, s = np.linalg.lstsq(A, b, rcond=None)

            # found a better estimation
            if error < best_error:
                count += 1 # for debugging
                best_loc = loc
                best_error = error
                best_X = X_array

        # return best_loc, [left_constraints, right_constraints] # for debugging
        best_loc = [best_loc[0][0], best_loc[1][0], best_loc[2][0]]
       
        all_dicts[file_num]['new_3d_pos'][0:3]=best_loc
        

In [85]:
cal_math(all_dicts['000004'])
all_dicts['000004']

/tmp/ipykernel_3205021/2284385980.py:106: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  A = np.zeros([4,3], dtype=np.float)
/tmp/ipykernel_3205021/2284385980.py:106: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  A = np.zeros([4,3], dtype=np.float)
/tmp/ipykernel_3205021/2284385980.py:106: DeprecationWarning: `np.float` is a deprecated ali

[{'class': 'Car',
  'alpha': 1.96,
  'boxs': [280.38, 185.1, 344.9, 215.59],
  '3d_attribute': [1.49, 1.76, 4.01, -15.71, 2.16, 38.26, 1.57],
  'new_3d_pos': [-15.632581189927409, 0.744285599673475, 38.136276438705615]},
 {'class': 'Car',
  'alpha': 1.88,
  'boxs': [365.14, 184.54, 406.11, 205.2],
  '3d_attribute': [1.38, 1.8, 3.41, -15.89, 2.23, 51.17, 1.58],
  'new_3d_pos': [-15.47575313321012, 0.6266314869635465, 50.140076973444025]},
 {'class': 'DontCare',
  'alpha': -10.0,
  'boxs': [402.27, 166.69, 477.31, 197.98],
  '3d_attribute': [-1.0, -1.0, -1.0, -1000.0, -1000.0, -1000.0, -10.0],
  'new_3d_pos': [1.8563892184680224, 0.05242574672702105, -8.373231051487647]},
 {'class': 'DontCare',
  'alpha': -10.0,
  'boxs': [518.53, 177.31, 531.51, 187.17],
  '3d_attribute': [-1.0, -1.0, -1.0, -1000.0, -1000.0, -1000.0, -10.0],
  'new_3d_pos': [4.79740249492, 0.1940319483371269, -42.28344407643229]},
 {'class': 'DontCare',
  'alpha': -10.0,
  'boxs': [1207.5, 233.35, 1240.0, 333.39],
  '3d

In [75]:
def corner_fine_tune(box_corner):
    if (box_corner[0]>box_corner[3]):
        box_corner[0],box_corner[3]=box_corner[3],box_corner[0]
    if (box_corner[2]>box_corner[5]):
        box_corner[2],box_corner[5]=box_corner[5],box_corner[2]
    return box_corner
class pred_Object3d(object):
    def __init__(self, data,data_num):
        self.alpha = float(data[data_num]['alpha'])
        self.box2d = np.array((float(data[data_num]['boxs'][0]), float(data[data_num]['boxs'][1]), float(data[data_num]['boxs'][2]), float(data[data_num]['boxs'][3])), dtype=np.float32)
        self.h = float(data[data_num]['3d_attribute'][0])
   
        self.w = float(data[data_num]['3d_attribute'][1])
        self.l = float(data[data_num]['3d_attribute'][2])
        self.loc = np.array((float(data[data_num]['new_3d_pos'][0]), float(data[data_num]['new_3d_pos'][1]), float(data[data_num]['new_3d_pos'][2])), dtype=np.float32)
    
        self.dis_to_cam = np.linalg.norm(self.loc)
        self.ry = float(data[data_num]['3d_attribute'][6])
      
    def generate_corners3d(self):
        """
        generate corners3d representation for this object
        :return corners_3d: (8, 3) corners of box3d in camera coord
        """
        l, h, w = self.l, self.h, self.w
        x_corners = [l / 2, l / 2, -l / 2, -l / 2, l / 2, l / 2, -l / 2, -l / 2]
        y_corners = [h/2, h/2, h/2, h/2, -h/2, -h/2, -h/2, -h/2]
        #y_corners = [0, 0, 0, 0, -h, -h, -h, -h]
        z_corners = [w / 2, -w / 2, -w / 2, w / 2, w / 2, -w / 2, -w / 2, w / 2]
        
        # rot_y
        R = np.array([[np.cos(self.ry), 0, np.sin(self.ry)],
                      [0, 1, 0],
                      [-np.sin(self.ry), 0, np.cos(self.ry)]])
        corners3d = np.vstack([x_corners, y_corners, z_corners])  # (3, 8)
        corners3d = np.dot(R, corners3d).T
        corners3d = corners3d + self.loc
        buttom =corners3d[0:4]
        buttom_center=(np.sum(buttom,axis=0)/4)
       #print('math',corners3d)
        corners3d=np.concatenate((corners3d[2,:],corners3d[4,:]),axis=0)
        corners3d= corner_fine_tune(corners3d)
        return corners3d,buttom_center
        



In [74]:


class Object3d(object):
    def __init__(self, data,data_num):
        self.class_type=data[data_num]['class']
        self.alpha = float(data[data_num]['alpha'])
        self.box2d =  np.array((float(data[data_num]['boxs'][0]), float(data[data_num]['boxs'][1]), float(data[data_num]['boxs'][2]), float(data[data_num]['boxs'][3])), dtype=np.float32)
        self.h = float(data[data_num]['3d_attribute'][0])
        self.w = float(data[data_num]['3d_attribute'][1])
        self.l = float(data[data_num]['3d_attribute'][2])
        self.loc = np.array((float(data[data_num]['3d_attribute'][3]), float(data[data_num]['3d_attribute'][4]), float(data[data_num]['3d_attribute'][5])), dtype=np.float32)
        self.dis_to_cam = np.linalg.norm(self.loc)
        self.ry = float(data[data_num]['3d_attribute'][6])
       
        
    def generate_corners3d(self):
        """
        generate corners3d representation for this object
        :return corners_3d: (8, 3) corners of box3d in camera coord
        """
        l, h, w = self.l, self.h, self.w
        x_corners = [l / 2, l / 2, -l / 2, -l / 2, l / 2, l / 2, -l / 2, -l / 2]
        y_corners = [0, 0, 0, 0, -h, -h, -h, -h]
        z_corners = [w / 2, -w / 2, -w / 2, w / 2, w / 2, -w / 2, -w / 2, w / 2]
        
        # rot_y
        R = np.array([[np.cos(self.ry), 0, np.sin(self.ry)],
                      [0, 1, 0],
                      [-np.sin(self.ry), 0, np.cos(self.ry)]])
        corners3d = np.vstack([x_corners, y_corners, z_corners])  # (3, 8)
        corners3d = np.dot(R, corners3d).T
        corners3d = corners3d + self.loc
        #print('origin',corners3d)
        corners3d=np.concatenate((corners3d[2,:],corners3d[4,:]),axis=0)
        corners3d =corner_fine_tune(corners3d)
        return corners3d




In [32]:
def iou_3d(box1,box2):
    '''box [x1,y1,z1,x2,y2,z2]'''
    area1=(box1[3]-box1[0])*(box1[4]-box1[1])*(box1[5]-box1[2])
    area2=(box2[3]-box2[0])*(box2[4]-box2[1])*(box2[5]-box2[2])
    area_sum =area1+area2
    #count overlap region assum overlapped box coordinate is [x1,y1,z1,x2,y2,z2]
    x1=max(box1[0],box2[0])
    y1=min(box1[1],box2[1])
    z1=max(box1[2],box2[2])
    x2=min(box1[3],box2[3])
    y2=max(box1[4],box2[4])
    z2=min(box1[5],box2[5])
    if x1>=x2 or y1<=y2 or z1 >= z2:
        return 0
    else :
        inter_area=(x2-x1)*(y2-y1)*(z2-z1)
    return inter_area/(area_sum-inter_area)


In [79]:
# origin_object=Object3d(all_dicts['000010'],0)
# math_object=pred_Object3d(all_dicts['000010'],0)
# math_corner,buttom=math_object.generate_corners3d()
# corner=(origin_object.generate_corners3d())
cal_math(all_dicts['000004'])
for i in range(len(all_dicts['000004'])):
    math_object=pred_Object3d(all_dicts['000004'],i)
    math_corner,buttom=math_object.generate_corners3d()
    print('buttom',buttom)



/tmp/ipykernel_3205021/2571353028.py:106: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  A = np.zeros([4,3], dtype=np.float)
/tmp/ipykernel_3205021/2571353028.py:106: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  A = np.zeros([4,3], dtype=np.float)
/tmp/ipykernel_3205021/2571353028.py:106: DeprecationWarning: `np.float` is a deprecated ali

buttom [-15.43791676   1.49841034  37.74583817]
buttom [-15.5245409    1.34406328  50.32653809]
buttom [ 1.85302043 -0.45772793 -8.37334633]
buttom [  4.77789211  -0.3198496  -42.38023376]
buttom [-2.98346663 -1.00991791 -3.39415121]
buttom [  4.81558418  -0.24187383 -52.34122849]
buttom [  3.31959677  -0.19468537 -54.75944519]


In [34]:
overlap_list=[]
depth_list=[]
for key,value in all_dicts.items():
    print(key)
    cal_math(all_dicts[key])
    for i in range(len(value)):
        if (all_dicts[key][i]['class']=='Car'):
            origin_object=Object3d(all_dicts[key],i)
            math_object=pred_Object3d(all_dicts[key],i)
            math_corner,math_buttom=math_object.generate_corners3d()
            corner=(origin_object.generate_corners3d())
            #print(float(math_corner[0][2])-float(corner[0][2]))
            #print(float(corner[2]))
            depth_list.append(math_corner[2]-corner[2])
            overlap_3d=iou_3d(corner,math_corner)
            print(overlap_3d)
            overlap_list.append(overlap_3d)
    
    #cal_math(all_dicts[key])

000000
000001
0.1386484377056281
000002
0.3435275390350684
000003
0.6935772118724473
000004
0.2577644743390387
0.11989332015914426
000005
000006
0.39628602546209846
0.15554463260761156
0.7630504061365138
0.3582763129745577
000007
0.45988437721872566
0.15589496808368075
0.10381919907365428
000008


/tmp/ipykernel_3205021/1332823770.py:100: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  A = np.zeros([4,3], dtype=np.float)


0
0.6507189473420899
0.19575957149816642
0.5792955197364404
0.14870964738232992
0.4930119340276021
000009
0.3850485289473879
0.07968362146640118
0.0520774455801518
000010
0
0.6417762620539532
0.6136092731101939
0.5295103224675973
0.442978185542402
0.32324940597666335
0.4358219444886034
0.18839936552228478
000011
0.4383639549004622
0
000012
0.12231752669039815
000013
0.48717595467949065
000014
0.11029860299850469
000015
0
000016
0.17667071211894178
0.29994166471490424
0
0.13369724759719637
000017
0.2890985281957201
000018
0.1720494747716673
000019
0.7573532941644093
0.08937345415603987
000020
0.6504293272746778
000021
0.6590628860156158
0.572280221887778
0.48023926331791766
0.42909592199059476
0.4548720241303286
0.3865507690285746
000022
0.3004742398134245
0.3567152485692831
000023
0.15823197322593233
000024
0.9550878587108438
0.7868404692261903
0.9493345547779523
000025
0
0.7222687079458903
0.3854850640307087
0.5886601775184899
0.47832317673247077
000026
0.09313260028746094
000027
0.00

In [54]:
#print(sum(overlap_list)/len(overlap_list))
print(len(overlap_list))
threshold=0.5
filtered_list=list(filter(lambda x: x > threshold,overlap_list))
print(overlap_list.count(0))
print(sum(overlap_list)/len(overlap_list))
print(len(filtered_list))
print(len(filtered_list)/28742)

28742
2785
0.3896561793003653
9765
0.3397467121285923


In [49]:
print(depth_list)
abs_depth_list=[abs(num) for num in depth_list]

[-0.8874969482421875, -0.29067230224609375, -0.134002685546875, -0.51416015625, -0.8434600830078125, -0.356170654296875, -0.17551231384277344, -0.05598640441894531, 0.06423568725585938, -0.3610687255859375, -0.8921546936035156, -1.0566482543945312, 3.416203260421753, -0.06334400177001953, 0.6240549087524414, -0.1024026870727539, -0.5532417297363281, -0.2920074462890625, -0.6948719024658203, -0.5365219116211009, -0.9628753662109375, 4.822278022766113, -0.12398147583007812, -0.2155609130859375, -0.1459789276123047, -0.3822765350341797, -0.6214771270751953, -0.10610389709472656, -0.8729400634765625, -0.4524421691894531, 11.535269737243652, -0.8091621398925781, -0.2910957336425781, -0.7355270385742188, 3.6273846626281734, -0.5595130920410156, -0.6116676330566406, 1.7595043182373047, -0.9356842041015625, -0.23883056640625, -1.0008697509765625, -0.09113788604736328, -1.6635475158691406, -0.03017425537109375, -0.07547569274902344, -0.2968921661376953, -0.11052703857421875, -0.4849052429199219

In [51]:
print(sum(abs_depth_list)/len(abs_depth_list))

1.1286985418400197
